In [41]:
"""
Gillespie model using Hendo et al. (2012) paper

'Bayesian emulation and calibration of a stochastic computer model of mitochondrial 
DNA deletions in sibstantia nigra neurons'
"""

"Gillespie model using Hendo et al. (2012) paper\n\n'Bayesian emulation and calibration of a stochastic computer model of mitochondrial \nDNA deletions in sibstantia nigra neurons'\n"

In [42]:
using Distributed

In [43]:
length(Sys.cpu_info())
addprocs(3) ;

In [44]:
@everywhere using Random, Distributions, Plots, DelimitedFiles

In [45]:
@everywhere struct SPN
    init::Vector{Real}
    k::Vector{Real}
    S::Array{Real}
    Tmax::Real
    dt::Real
    function SPN(init, k, S, Tmax, dt)
        new(init, k, S, Tmax, dt)
    end
end

In [46]:
@everywhere init(N::SPN) = Float64.(N.init)
@everywhere rates(N::SPN) = Float64.(N.k)
@everywhere S(N::SPN) = Float64.(N.S)
@everywhere Tmax(N::SPN) = Float64.(N.Tmax)
@everywhere dt(N::SPN) = Float64.(N.dt)
@everywhere n(N::SPN) = trunc(Int, N.Tmax/N.dt)

In [47]:
# c0: given in the paper as 1000, I think it's mean to be close to the intial copy number 
# however cannot find the supplementary material, where its derivation is explained 
@everywhere function hazard(x::Vector{Float64}, th::Vector{Float64}, c0)::Vector{Float64}
    [th[1]*x[1], c0*th[2]*x[1]/sum(x), th[2]*x[1], c0*th[2]*x[2]/sum(x), th[2]*x[2]]
end

In [48]:
@everywhere const post = [[0,2,0,0,0] [1,0,0,2,0]]
@everywhere const pre = [[1,1,1,0,0] [0,0,0,1,1]]
@everywhere const SS = post - pre
@everywhere const kk = [exp(-10.18), exp(-4.58), 0.962]; # per day

      From worker 2:	WARNING: redefinition of constant post. This may fail, cause incorrect answers, or produce other errors.
      From worker 3:	WARNING: redefinition of constant post. This may fail, cause incorrect answers, or produce other errors.
      From worker 4:	WARNING: redefinition of constant post. This may fail, cause incorrect answers, or produce other errors.


      From worker 3:	WARNING: redefinition of constant pre. This may fail, cause incorrect answers, or produce other errors.
      From worker 2:	WARNING: redefinition of constant pre. This may fail, cause incorrect answers, or produce other errors.
      From worker 4:	WARNING: redefinition of constant pre. This may fail, cause incorrect answers, or produce other errors.
      From worker 2:	WARNING: redefinition of constant SS. This may fail, cause incorrect answers, or produce other errors.
      From worker 3:	WARNING: redefinition of constant SS. This may fail, cause incorrect answers, or produce other errors.
      From worker 4:	WARNING: redefinition of constant SS. This may fail, cause incorrect answers, or produce other errors.


      From worker 3:	WARNING: redefinition of constant kk. This may fail, cause incorrect answers, or produce other errors.
      From worker 2:	WARNING: redefinition of constant kk. This may fail, cause incorrect answers, or produce other errors.
      From worker 4:	WARNING: redefinition of constant kk. This may fail, cause incorrect answers, or produce other errors.


In [49]:
@everywhere function gen_inits(μ::Real, σ::Real, α::Real, β::Real)::Vector{Float64}
    CC = rand(Normal(μ, σ))
    hh = rand(Beta(α, β))
    return round.( [CC*(1-hh), CC*hh] )
end

"""
When specifying the parameters as ::Float64 the function is consistently a slower
...weird but okay.
"""

"When specifying the parameters as ::Float64 the function is consistently a slower\n...weird but okay.\n"

In [50]:
@everywhere function gillespied(N)
    c = rates(N)
    x = init(N)
    δt = dt(N)
    nn = n(N)
    SS = S(N)
    tt = 0.0
    xmat = Array{Any}(undef, (2,nn))
    i = 1
    target = 0.0
    C0 = sum(x)
    while i <= nn
        h = hazard(x, c, C0)
        h0 = sum(h)
        if h0<1e-10
            xmat[:,i:nn] = fill(0.0, (2,nn-i+1))
            return xmat'
        elseif x[2]/sum(x)>=c[3]
            xmat[:,i:nn] = fill(missing, (2,nn-i+1))
            return xmat'
        else
            Exp = Exponential(1/h0)
            tt = tt + rand(Exp)
        end
        while tt>=target && i<=nn
            xmat[:,i] = x
            i += 1
            target += δt
        end
        Cat = Categorical(h/h0)
        r = rand(Cat)
        x += SS'[:,r]
    end
    return xmat'
end

In [51]:
@everywhere function replace_nan(x)
    """
    replaces NaN's caused by 0/0 in mutation load calculation
    """
    for i=eachindex(x)
        x[i] = isnan(x[i]) ? missing : x[i]
    end
end

In [52]:
@everywhere function raw_to_summ(sims)::Array{Any}
    """
    converts the species populations from the gillespie algorithm to 
    copy number and mutation load
    """
    Nsim = size(sims)[3] # no. of simulations
    n = size(sims)[1] # length of one simulation
    out = Array{Any}(undef, (n,2,Nsim) )
    for i=1:Nsim
        copy_num = sims[:,1,i] .+ sims[:,2,i]
        mut_load = sims[:,2,i]./copy_num
        # replace_nan(copy_num)
        # replace_nan(mut_load)
        out[:,:,i] = hcat(copy_num, mut_load)
    end
    out
end

In [53]:
@everywhere function quantiles(sims, p)
    """
    returns quantile summaries from simulations
    """
    Nsim = size(sims)[3] # Nsim: number of simulations
    n = size(sims)[1] # length of one simulation
    out = Array{Float64}(undef, n,length(p),2)
    for t=1:n
        out[t,:,1] = quantile(skipmissing([sims[t,1,i] for i=1:Nsim]), p)
        out[t,:,2] = quantile(skipmissing([sims[t,2,i] for i=1:Nsim]), p)
    end
    out
end

In [54]:
@everywhere Nsim = 500
@everywhere Tsim = 80*365
@everywhere δt = 1 ; 

In [55]:
initial_logCN = rand(Normal(10.59, 1.07)) # parameters taken from Rocha data
initial_ML = 0 
Ntest = SPN([exp(initial_logCN)*(1-initial_ML),exp(initial_logCN)*initial_ML], kk, SS, Tsim, δt)
@time gillespied(Ntest);
"""
a single run (C_0=200) takes ~0.7 seconds
a single run (C_0 = exp(11), logC_0~Norm(10.59, 1.07)) takes ~12 seconds
"""

 15.832271 seconds (272.82 M allocations: 13.767 GiB, 13.87% gc time, 0.93% compilation time)


"a single run (C_0=200) takes ~0.7 seconds\na single run (C_0 = exp(11), logC_0~Norm(10.59, 1.07)) takes ~12 seconds\n"

In [56]:
"""
simulations_single = Array{Float64}(undef, n(Ntest), 2, Nsim)
@time for i=1:Nsim
    simulations_single[:,:,i] = gillespied(Ntest)
end
This is a lot slower (doubly slow) than the previous version without the SPN structure
For 1000 simulations 26.536 seconds
"""

"simulations_single = Array{Float64}(undef, n(Ntest), 2, Nsim)\n@time for i=1:Nsim\n    simulations_single[:,:,i] = gillespied(Ntest)\nend\nThis is a lot slower (doubly slow) than the previous version without the SPN structure\nFor 1000 simulations 26.536 seconds\n"

In [57]:
#summ_single = raw_to_summ(simulations_single);
#qnts_single = quantiles(summ_single, [0.025,0.1,0.5,0.9,0.975]) ;

In [58]:
# The arguments are: 1) a function 'f' and 2) a list with the input.
@everywhere function simulation_map(f, lst)
    np = nworkers()            # Number of processes available.
    Nsim  = length(lst)  # Number of elements to apply the function.
    nn = n(lst[1]) # dimension for output
    output = Array{Any}(undef, nn,2,Nsim) # Where we will write the results. As we do not know
                             # the type (Integer, Tuple...) we write "Any"
    i = 1
    nextidx() = (idx = i; i += 1; idx) # Function to know which is the next work item.
                                       # In this case it is just an index.
    @sync begin #@sync: must complete all jobs in block
        for p = 1:np # loops through all processes (workers)
            if p != myid() || np == 1 # first worker used only if all others are busy 
                @async begin # launch several tasks simultaneaously
                    while true
                        idx = nextidx()
                        if idx > Nsim
                            break
                        end
                        output[:,:,idx] = fetch(remotecall(f, p, lst[idx]))
                    end
                end
            end
        end
    end
    output
end

In [59]:
initial_logCN = rand(Normal(10.59, 1.07))
initial_ML = 0 
Ntest = SPN([initial_logCN*(1-initial_ML),initial_logCN*initial_ML], kk, SS, Tsim, δt)
N_lst = [ Ntest for i=1:Nsim ] ;

In [60]:
@time raw_simulations = simulation_map(gillespied, N_lst) ;
"""
1000 simulations (hendo et al. params): 24 s
"""

LoadError: TaskFailedException

[91m    nested task error: [39mOn worker 2:
    ArgumentError: Categorical: the condition isprobvec(p) is not satisfied.
    Stacktrace:
     [1] [0m[1mmacro expansion[22m
    [90m   @ [39m[90m~/.julia/packages/Distributions/1WSG5/src/[39m[90;4mutils.jl:6[0m[90m [inlined][39m
     [2] [0m[1m#_#48[22m
    [90m   @ [39m[90m~/.julia/packages/Distributions/1WSG5/src/univariate/discrete/[39m[90;4mcategorical.jl:30[0m[90m [inlined][39m
     [3] [0m[1m#Categorical#49[22m
    [90m   @ [39m[90m~/.julia/packages/Distributions/1WSG5/src/univariate/discrete/[39m[90;4mcategorical.jl:34[0m[90m [inlined][39m
     [4] [0m[1mDiscreteNonParametric[22m
    [90m   @ [39m[90m~/.julia/packages/Distributions/1WSG5/src/univariate/discrete/[39m[90;4mcategorical.jl:34[0m[90m [inlined][39m
     [5] [0m[1mgillespied[22m
    [90m   @ [39m[90m./[39m[90;4mIn[50]:30[0m
     [6] [0m[1m#103[22m
    [90m   @ [39m[90m/Users/julia

In [61]:
simulations = raw_to_summ(raw_simulations);

In [62]:
sims_qntl = quantiles(simulations, [0.025,0.25,0.5,0.75,0.975]) ;

In [63]:
simulations = raw_to_summ(raw_simulations);
sims_qntl = quantiles(simulations, [0.025,0.25,0.5,0.75,0.975]) ;

In [64]:
writedlm("Simulations/CN_qnt_gillHend_jl.txt", sims_qntl[:,:,1])
writedlm("Simulations/ML_qnt_gillHend_jl.txt", sims_qntl[:,:,2])

In [65]:
function distributions_t(sims, t, Tsim, δt)
    t_tot = [δt:δt:Tsim;]
    Nsim = size(sims)[3]
    nt = length(t)
    sim_t = Array{Any}(undef, Nsim,nt,2)
    for i=1:Nsim
        for j=1:nt
            sim_t[i,j,1] = sims[findall(x->x==t[j], t_tot),1,i][1]
            sim_t[i,j,2] = sims[findall(x->x==t[j], t_tot),2,i][1]
        end
    end
    sim_t
end


distributions_t (generic function with 1 method)

In [66]:
dist_sims = distributions_t(simulations, [10:10:80;]*365, Tsim, δt) ;

In [67]:
writedlm("Simulations/hendo_CN_ts_gill_jl.txt", dist_sims[:,:,1])
writedlm("Simulations/hendo_ML_ts_gill_jl.txt", dist_sims[:,:,2])

In [68]:
myBlack = colorant"rgb(0,0,0,0.1)"
ts = [1:δt:Tsim;]./365;

In [69]:
p3 = plot(ts, sims_qntl[:,:,1], title="Copy Number Qunatiles")
p4 = plot(ts, sims_qntl[:,:,2], title="Mutation Load Quantiles")
plot(p3, p4, layout=(1,2), legend=false)